In [1]:
import mwapi
import pprint
import pandas as pd
import numpy as np
import plotly.express as ex
import matplotlib.pyplot as plt

pp = pprint.PrettyPrinter()

## API to dataframe
This section was run and a csv file was created and saved. Therefore it is not required to be run again. The extract_source.py file can be used to generate the csv.

In [10]:
session = mwapi.Session('https://en.wikipedia.org', user_agent='aysha.kamal7')

In [23]:
data_list = []
missed = []
_gapcontinue = ''
_revcontinue = ''
_continue = ''
while True:
    params = {'action':'query',
            'generator':'allpages',
            'gapnamespace':828,
            'gaplimit':'max',
            'format':'json',
            'prop':'info',
            'inprop':'url',
            'gapcontinue': _gapcontinue,
            'continue': _continue,
            }
    
    result = session.get(params)

    for page in list(result['query']['pages'].values()):
        try:
            
            pageid = page['pageid']
            title = page['title']
            touched = page['touched']
            length = page['length']
            url = page['fullurl']
            revid = page['lastrevid']
            
            params = {'action':'query',
                    'format':'json',
                    'prop':'revisions',
                    'revids':revid,
                    'rvprop':'content',
                    'rvslots':'main',
                    # 'rvlimit':1,
                    # 'rvdir':'newer',
                    'formatversion':2
                    }
    
            rev_result = session.get(params)

            content_info = rev_result['query']['pages'][0]['revisions'][0]['slots']['main']
            content = content_info['content']
            content_model = content_info['contentmodel']
            content_format = content_info['contentformat']
            
            data_list.append([pageid, title, url, length, content, content_format, content_model, touched])
        except:
            if 'title' in page.keys():
                missed+=page['title']

    try:
        _continue = result['continue']['continue']
        _gapcontinue = result['continue']['gapcontinue'] \
            if 'gapcontinue' in  result['continue'] else ''
        # _revcontinue = result['continue']['gapcontinue'] if 'gapcontinue' in  result['continue'] else ''        
    except:
        break
    
    print(len(data_list))
    # if len(data_list)>10:
    #     break

In [19]:
result

{'batchcomplete': '',
 'limits': {'allpages': 500},
 'query': {'pages': {'38665046': {'pageid': 38665046,
    'ns': 828,
    'title': 'Module:Yesno',
    'contentmodel': 'Scribunto',
    'pagelanguage': 'en',
    'pagelanguagehtmlcode': 'en',
    'pagelanguagedir': 'ltr',
    'touched': '2020-10-13T09:33:49Z',
    'lastrevid': 948473803,
    'length': 745,
    'fullurl': 'https://en.wikipedia.org/wiki/Module:Yesno',
    'editurl': 'https://en.wikipedia.org/w/index.php?title=Module:Yesno&action=edit',
    'canonicalurl': 'https://en.wikipedia.org/wiki/Module:Yesno'},
   '40585364': {'pageid': 40585364,
    'ns': 828,
    'title': 'Module:Yesno/doc',
    'contentmodel': 'wikitext',
    'pagelanguage': 'en',
    'pagelanguagehtmlcode': 'en',
    'pagelanguagedir': 'ltr',
    'touched': '2020-10-11T07:06:01Z',
    'lastrevid': 966506722,
    'length': 3401,
    'fullurl': 'https://en.wikipedia.org/wiki/Module:Yesno/doc',
    'editurl': 'https://en.wikipedia.org/w/index.php?title=Module:Yes

In [13]:
data_list[0]

[39127846,
 'Module:AFC submission catcheck',
 'https://en.wikipedia.org/wiki/Module:AFC_submission_catcheck',
 1122,
 'local p = {}\n\nlocal function removeFalsePositives(str)\n\tif not str then\n\t\treturn \'\'\n\tend\n\tstr = mw.ustring.gsub(str, "<!--.--->", "")\n\tstr = mw.ustring.gsub(str, "<nowiki>.-</nowiki>", "")\n\tstr = mw.ustring.gsub(str, "{{[Dd]raft categories[^{}]-{{[^{}]-}}[^{}]-}}", "")\n\tstr = mw.ustring.gsub(str, "{{[Dd]raft categories.-}}", "")\n\tstr = mw.ustring.gsub(str,"%[%[Category:Unsuitable for Wikipedia AfC submissions%]%]","")\n\tstr = mw.ustring.gsub(str,"%[%[Category:[Dd]rafts.-%]%]","")\n\tstr = mw.ustring.gsub(str,"%[%[Category:.-drafts%]%]","")\n\treturn str\nend\n\nfunction p.checkforcats(frame)\n    local t = mw.title.getCurrentTitle()\n    tc = t:getContent()\n    if tc == nil then \n        return ""\n    end\n    tc = removeFalsePositives(tc)\n    if mw.ustring.match(tc, "%[%[%s-[Cc]ategory:" ) == nil then\n        return ""\n    else\n        re

In [24]:
len(missed)

0

In [25]:
len(data_list)

12507

In [16]:
## Create the dataframe
data_df = pd.DataFrame(data_list, columns=['id', 'title', 'url', 'length', 'content', 'format', 'model', 'touched'])

In [17]:
data_df.head()

id                                        title  \
0  39127846               Module:AFC submission catcheck   
1  43996534           Module:AFC submission catcheck/doc   
2  57798447       Module:AFC submission catcheck/sandbox   
3  59702564      Module:AFC submission catcheck/sandbox2   
4  62753335  Module:AFC submission catcheck/sandbox2/doc   

                                                 url  length  \
0  https://en.wikipedia.org/wiki/Module:AFC_submi...    1122   
1  https://en.wikipedia.org/wiki/Module:AFC_submi...     511   
2  https://en.wikipedia.org/wiki/Module:AFC_submi...    1075   
3  https://en.wikipedia.org/wiki/Module:AFC_submi...     826   
4  https://en.wikipedia.org/wiki/Module:AFC_submi...      48   

                                             content       format      model  \
0  local p = {}\n\nlocal function removeFalsePosi...   text/plain  Scribunto   
1  {{module rating|protected}}\n<!-- Categories g...  text/x-wiki   wikitext   
2  local p = {}\n\nlocal function removeFalsePosi...   text/plain  Scribunto   
3  local p = {}\n\nlocal function removeFalsePosi...   text/plain  Scribunto   
4   #REDIRECT [[Module:AFC submission catcheck/doc]]  text/x-wiki   wikitext   

                touched  
0  2020-10-13T09:33:55Z  
1  2020-09-29T03:40:40Z  
2  2020-10-13T09:36:19Z  
3  2020-10-13T09:36:37Z  
4  2020-01-05T21:57:04Z

In [18]:
## Save dataframe
data_df.to_csv('wiki_ns.csv', index=False)

## Load csv and perform data analysis

In [2]:
df = pd.read_csv('wiki_ns.csv')
df.head()

id                                        title  \
0  39127846               Module:AFC submission catcheck   
1  43996534           Module:AFC submission catcheck/doc   
2  57798447       Module:AFC submission catcheck/sandbox   
3  59702564      Module:AFC submission catcheck/sandbox2   
4  62753335  Module:AFC submission catcheck/sandbox2/doc   

                                                 url  length  \
0  https://en.wikipedia.org/wiki/Module:AFC_submi...    1122   
1  https://en.wikipedia.org/wiki/Module:AFC_submi...     511   
2  https://en.wikipedia.org/wiki/Module:AFC_submi...    1075   
3  https://en.wikipedia.org/wiki/Module:AFC_submi...     826   
4  https://en.wikipedia.org/wiki/Module:AFC_submi...      48   

                                             content       format      model  \
0  local p = {}\n\nlocal function removeFalsePosi...   text/plain  Scribunto   
1  {{module rating|protected}}\n<!-- Categories g...  text/x-wiki   wikitext   
2  local p = {}\n\nlocal function removeFalsePosi...   text/plain  Scribunto   
3  local p = {}\n\nlocal function removeFalsePosi...   text/plain  Scribunto   
4   #REDIRECT [[Module:AFC submission catcheck/doc]]  text/x-wiki   wikitext   

                touched  
0  2020-10-13T09:33:55Z  
1  2020-09-29T03:40:40Z  
2  2020-10-13T09:36:19Z  
3  2020-10-13T09:36:37Z  
4  2020-01-05T21:57:04Z

### File types analysis

In [28]:
df['format'].value_counts()

text/plain         7621
text/x-wiki        4866
text/css             19
text/javascript       1
Name: format, dtype: int64

In [29]:
df['model'].value_counts()

Scribunto        7621
wikitext         4866
sanitized-css      19
javascript          1
Name: model, dtype: int64

In [4]:
df[df['format']=='text/plain']['title']

0                  Module:AFC submission catcheck
2          Module:AFC submission catcheck/sandbox
3         Module:AFC submission catcheck/sandbox2
5        Module:AFC submission catcheck/testcases
6                                Module:AFC topic
                           ...                   
12500                                Module:Yesno
12502                        Module:Yesno/sandbox
12503                      Module:Yesno/testcases
12504                                   Module:Zh
12505                          Module:Zodiac date
Name: title, Length: 7621, dtype: object

In [31]:
df[df['format']=='text/x-wiki']['title']

1                 Module:AFC submission catcheck/doc
4        Module:AFC submission catcheck/sandbox2/doc
7                               Module:AFC topic/doc
10              Module:ATC code to template name/doc
12                            Module:AWBVersions/doc
                            ...                     
12493           Module:Year in various calendars/doc
12496                     Module:Years generator/doc
12498       Module:Yemeni Civil War detailed map/doc
12501                               Module:Yesno/doc
12506                         Module:Zodiac date/doc
Name: title, Length: 4866, dtype: object

In [9]:
## Lets check if all /doc docuemnts are of x-wiki format
df[df['title'].apply(lambda x: x[-3:]=='doc')]['format'].unique()

array(['text/x-wiki', 'text/plain'], dtype=object)

In [33]:
df[df['format']=='text/css'].head()

id                                   title  \
787   60213274         Module:Archive index/styles.css   
833   63189587     Module:Authority control/styles.css   
879   63654683               Module:Bar box/styles.css   
1077  58177736  Module:Citation/CS1/sandbox/styles.css   
1083  57940169          Module:Citation/CS1/styles.css   

                                                    url  length  \
787   https://en.wikipedia.org/wiki/Module:Archive_i...      42   
833   https://en.wikipedia.org/wiki/Module:Authority...     333   
879   https://en.wikipedia.org/wiki/Module:Bar_box/s...     399   
1077  https://en.wikipedia.org/wiki/Module:Citation/...    3345   
1083  https://en.wikipedia.org/wiki/Module:Citation/...    3290   

                                                content    format  \
787       tr:nth-child(2n) {\n\tbackground: #dddddd;\n}  text/css   
833   @media screen and (max-width: 719px) {\n\t.aut...  text/css   
879   /* {{pp-template}} */\n.bb-min3{\n\tmin-width:...  text/css   
1077  /*\nHistory of changes since last sync: 2020-1...  text/css   
1083  /* Protection icon\nthe following line control...  text/css   

              model               touched  
787   sanitized-css  2019-03-13T01:41:23Z  
833   sanitized-css  2020-04-12T00:56:39Z  
879   sanitized-css  2020-09-29T03:41:01Z  
1077  sanitized-css  2020-10-10T15:28:23Z  
1083  sanitized-css  2020-10-10T13:22:51Z

In [29]:
## utility function to help plot bar charts
def df_to_count(_df, col):
    count_df = pd.DataFrame(_df[col].value_counts()).reset_index()
    count_df.columns = [col, 'count']
    return count_df

In [32]:
df_to_count(df, 'format')

format  count
0       text/plain   7621
1      text/x-wiki   4866
2         text/css     19
3  text/javascript      1

In [48]:
## Distribution of the file formats
ex.bar(df_to_count(df, 'format'), x='format', y='count', labels={'format':'file format'}
        , title='Distribution of the different file formats').update(layout=dict(title=dict(x=0.5)))

### Modules

In [24]:
import re
pat = re.compile('^Module:([^/]*)/(.*)')

In [142]:
titles = df['title'].apply(lambda x: pat.match(x+'/').group(1))

In [143]:
titles.nunique()

850

In [144]:
titles.unique()[-10:]

array(['XfD old', 'Xiangqi-position', 'Xpsoc', 'YMD to ISO',
       'Year in various calendars', 'Years generator',
       'Yemeni Civil War detailed map', 'Yesno', 'Zh', 'Zodiac date'],
      dtype=object)

In [145]:
tops = titles.value_counts()[:50]
tops

Location map              6275
Sandbox                   1424
Adjacent stations          702
ISO 3166                   508
Road data                  322
Portal                      91
Language                    66
Find sources                65
Unicode data                53
Citation                    49
Sports table                43
Infobox road                37
Convert                     33
Transclusion count          32
User:Mr. Stradivarius       32
Lang                        32
Goalscorers                 25
Solar eclipse               22
WikiProjectBanner           22
Signpost                    21
Sports color                20
IPA symbol                  20
ISO 639 name                18
SportsRankings              17
Calendar date               14
User:AmazingJus             14
Wd                          14
IPAc-en                     14
Footnotes                   14
Taxonbar                    13
Wikipedia ads               13
Jct                         12
UserLink

In [146]:
titles.value_counts()[-10:]

Israeli-Palestinian localities           1
User:Mr rnddude                          1
Navseasoncats with decades below year    1
User:Plagiat                             1
Iranian insurgency detailed map          1
User:Dragons flight                      1
Fb                                       1
Single ratings                           1
Stationlist row                          1
Infobox video game awards                1
Name: title, dtype: int64

In [47]:
ex.bar(tops, labels={'value':'count', 'index':'module'}, 
        title='Distribution of #files in the modules').update(layout=dict(title=dict(x=0.5)))

### Identify special titles

sandbox, user, Language vs Lang vs Lang-hbs, Wd, Flagg, WD, Su

In [47]:
users = titles[titles.apply(lambda x: x[:5]=='User:')]
user_vals = users.value_counts()
user_vals

User:Mr. Stradivarius        32
User:AmazingJus              14
User:DePiep                  12
User:Fred Gandt               4
User:Happy5214                4
User:Lesser Cartographies     4
User:Huhu9001                 4
User:Anomie                   3
User:SuggestBot               2
User:Martijn Hoekstra         2
User:AnomieBOT                2
User:Plagiat                  1
User:Mr rnddude               1
User:Alexiscoutinho           1
User:Ketil3                   1
User:Dcoetzee                 1
User:Mxn                      1
User:Doc Taxon                1
User:Vuh                      1
User:TeleComNasSprVen         1
User:Awesomemeeos             1
User:Legoktm                  1
User:Dragons flight           1
User:Kephir                   1
User:Yair rand                1
Name: title, dtype: int64

In [48]:
len(users), len(user_vals)

(97, 25)

In [151]:
ending = df['title'].apply(lambda x: pat.match(x+'/').group(2))
suffixes = ending[ending.apply(lambda x: len(x)>1)]
nosuffixes = titles[ending.apply(lambda x: len(x)<=1)]
len(suffixes), len(nosuffixes)

(11688, 819)

In [152]:
len(nosuffixes.value_counts()), len(suffixes.value_counts())

(819, 10175)

In [153]:
suffixes.value_counts()[:10]

doc/             700
sandbox/         399
testcases/       150
data/             62
data/doc/         36
sandbox2/         23
config/           20
data/sandbox/     18
config/doc/       14
styles.css/       10
Name: title, dtype: int64

In [131]:
ex.bar(suffixes.value_counts()[:50], labels={'value':'count', 'index':'suffix'}, 
        title='Distribution of top file suffixes').update_layout(title=dict(x=0.5), showlegend=False)

In [159]:
## Combine similar suffixes
# first separate /doc
docs = suffixes[suffixes.apply(lambda x: x[-4:]=='doc/')]
rest = suffixes[~suffixes.apply(lambda x: x[-4:]=='doc/')]
docs.value_counts()

doc/                                700
data/doc/                            36
config/doc/                          14
sandbox2/doc/                         7
sandbox/doc/                          6
                                   ... 
data/CAN AB Saddle Hills/doc/         1
data/Jerusalem East Central/doc/      1
data/Slovakia Trnava Region/doc/      1
data/BV/doc/                          1
data/India Jharkhand/doc/             1
Name: title, Length: 4078, dtype: int64

In [160]:
len(docs), docs.nunique()

(4849, 4078)

In [161]:
# separate /sandbox
sandbox_pat = re.compile('.*([Ss]andbox\d*)/.*')
sandbox = rest[rest.apply(lambda x: not sandbox_pat.match(x) is None)]
rest = rest[rest.apply(lambda x: sandbox_pat.match(x) is None)]
sandbox.value_counts()

sandbox/                           399
sandbox2/                           23
data/sandbox/                       18
sandbox/testcases/                  10
config/sandbox/                      7
                                  ... 
data/Charlotte/sandbox/              1
Taiwan High Speed Rail/sandbox/      1
Pennsylvania Railroad/sandbox/       1
data/India Jharkhand/sandbox/        1
Davykamanzi/sandbox/                 1
Name: title, Length: 260, dtype: int64

In [162]:
len(sandbox), sandbox.nunique()

(724, 260)

In [163]:
# separate /testcases
testcases = rest[rest.apply(lambda x: x[-10:]=='testcases/')]
rest = rest[~rest.apply(lambda x: x[-10:]=='testcases/')]
testcases.value_counts()[:10]

testcases/                             150
Erutuon/author citation/testcases/       1
isaacl/ColourSpace/Tuple/testcases/      1
Nyoron/anyToString/testcases/            1
data/Jordan/testcases/                   1
Biggins/LDSverseWS/testcases/            1
Rprimus06/Second/testcases/              1
Andy M. Wang/testcases/                  1
Wnt/FindFeatures/testcases/              1
Χ/InfoboxMaker/testcases/                1
Name: title, dtype: int64

In [164]:
len(testcases), testcases.nunique()

(208, 59)

In [99]:
# separate data/
data_pat = re.compile('.*data/.*')
data = rest[rest.apply(lambda x: not data_pat.match(x) is None)]
rest = rest[rest.apply(lambda x: data_pat.match(x) is None)]
data.value_counts()

data/                                   62
data/Futuna/                             1
data/people/                             1
data/Indonesia Maluku/                   1
data/United Kingdom Bristol Central/     1
                                        ..
data/NG/                                 1
data/Scotland South Ayrshire/            1
data/CAN BC Nanaimo/                     1
data/Greece Athens central/              1
data/France Caen/                        1
Name: title, Length: 3577, dtype: int64

In [165]:
len(data), data.nunique()

(3638, 3577)

In [102]:
rest.value_counts()[:20]

config/           20
styles.css/       10
i18n/              4
conf/              4
extra/             3
BHG-test/          3
core/              3
convert/           3
example/           3
contrast/          3
documentation/     3
shared/            3
display/           3
Chess/             2
pronunciation/     2
configuration/     2
phonemes/          2
list/              2
aliases/           2
colors/            2
Name: title, dtype: int64

In [166]:
len(rest), rest.nunique()

(5907, 5778)

In [130]:
## Show all as plot

vals = [docs, sandbox, testcases, data, rest]
titles = 'Distribution of top {} file suffixes'
valnames = ['docs', 'sandbox', 'testcases', 'data', 'remaining']

for val, valname in zip(vals,valnames):
    ex.bar(val.value_counts()[:10], labels={'value':'count', 'index':'suffix'}, 
            title=titles.format(valname)) \
            .update_layout(title=dict(x=0.5), showlegend=False, width=400, height=500,
            autosize=False,margin=dict(l=50,r=50,b=100,t=100,pad=4)) \
            .show()

### File size

In [21]:
df['length'].value_counts()[:10]

38     255
42     141
356     68
55      66
170     61
162     60
146     60
360     60
359     60
355     58
Name: length, dtype: int64

In [22]:
df['length'].value_counts()[-10:]

29962    1
1284     1
15619    1
83196    1
19701    1
1268     1
1260     1
25824    1
3293     1
6025     1
Name: length, dtype: int64

In [40]:
ex.histogram(df, x='length', labels={'length':'size in bytes'},
title = 'Histogram of file sizes').update(layout=dict(title=dict(x=0.5)))

In [49]:
shorts = df[df['length']<5000]

In [50]:
ex.histogram(shorts, x='length', labels={'length':'size in bytes'}, 
            title = 'Histogram of file sizes below 5k').update(layout=dict(title=dict(x=0.5)))

In [51]:
ex.histogram(shorts, x='length', labels={'length':'size in bytes'}, color='format',
            title = 'Histogram of file sizes by file format').update(layout=dict(title=dict(x=0.5)))

### Recent revisions

In [57]:
top50modules = list(tops.index)

In [69]:
top20modules = top50modules[:20]

In [49]:
df['module'] = df['title'].apply(lambda x: pat.match(x+'/').group(1))

In [76]:
## which modules were revised recently
## here we observe the top 20 modules with the most files
ex.scatter(df[df['module'].isin(top20modules)], x='touched', y='module', 
        title='Latest revision times of top 20 modules').update(layout=dict(title=dict(x=0.5)))

In [88]:
## here we observe all the files
## for spacing causes all module names are not displayed, 
## hover over a point to get it's information; zooming in shows more module names
ex.scatter(df, x='touched', y='module', 
    title='Latest revision times of all modules').update(layout=dict(title=dict(x=0.5)))

In [87]:
## Viewing 2020 revisions only
ex.scatter(df[df['touched']>='2020'], x='touched', y='module',
    title='Latest revision times of all modules in 2020').update(layout=dict(title=dict(x=0.5)))

We can see there distint lines, infact zoomin further to see 4-5 lines. These show us that on some days a large number of modules were edited. It can be any file for each of the modules.

In [86]:
## Files of which format were revised more recently
ex.scatter(df, x='touched', y='format',
    title='Latest revision times of different file formats').update(layout=dict(title=dict(x=0.5)))

This shows that x-wiki files are sometimes not revised often. Some latest revisions date back to 2014. Almost all code files, i.e text/plain files have been revised recently.

### Correlation of file size

In [89]:
ex.scatter(df, x='length', y='module',
        title='Correlation of file size and module').update(layout=dict(title=dict(x=0.5)))

In [90]:
ex.scatter(df, x='length', y='format',
        title='Correlation of file size and format').update(layout=dict(title=dict(x=0.5)))

text/plain files seem to come in all sizes whereas text/wiki files are usually small in size.